In [1]:
from __future__ import print_function
import findspark
findspark.init()

from pyspark.sql import SparkSession
from pyspark.mllib.regression import LabeledPoint
from pyspark.mllib.tree import DecisionTree, DecisionTreeModel
from numpy import array
import pandas as pd
import csv
import numpy as np
import warnings
warnings.filterwarnings('ignore')

In [2]:
from __future__ import print_function
spark = SparkSession.builder.appName('player-clustering').getOrCreate()

Bat_Clus = spark.read.options(header="true",
                               inferSchema="true",
                               nullValue="-",
                               mode="failfast").csv("Batting_Clusters.csv")

Bowl_Clus = spark.read.options(header="true",
                               inferSchema="true",
                               nullValue="-",
                               mode="failfast").csv("Bowling_Clusters.csv")

Over_Data = spark.read.options(header="true",
                               inferSchema="true",
                               nullValue="-",
                               mode="failfast").csv("Over_Data.csv")

In [3]:
Over_Data.head()
Bowl_Clus = Bowl_Clus.toPandas()
Bat_Clus = Bat_Clus.toPandas()
Bowl_Clus.fillna(0)
Bat_Clus.fillna(0)
Bat_Clus.head()
Bowl_Clus.head()

Player Name  Runs/Wickets   Economy  Balls bowled/wickets  \
0  A Ashish Reddy     22.000000  9.209302             14.333333   
1      A Chandila     22.000000  6.205128             21.272727   
2     A Choudhary     28.800000  8.727273             19.800000   
3      A Flintoff     52.500000  9.545455             33.000000   
4        A Kumble     23.511111  6.591900             21.400000   

   wickets/innings  
0         0.900000  
1         0.916667  
2         1.000000  
3         0.666667  
4         1.071429

In [4]:
Over_df = Over_Data.rdd.repartition(5).toDF()
Over_df.fillna(0)
Over_df=Over_df.drop('Batsman')
Over_df=Over_df.drop('Bowler')
Over_df=Over_df.drop('NonStriker')
Over_R = Over_df.drop('TotalWickets')
Over_W = Over_df.drop('TotalRuns')
Over_W = Over_W.rdd
Over_R = Over_R.rdd
print(type(Over_W))

<class 'pyspark.rdd.RDD'>


In [5]:
def flatten(aList):
    t = []
    for i in aList:
        if not isinstance(i, list):
             t.append(i)
        else:
             t.extend(flatten(i))
    return t

def train_create(vec):
    res = vec[1]
    
    feat = []
    feat.append(vec[0])
    feat = feat + list(vec[2:])
    feat = flatten(feat)
    return LabeledPoint(res,feat)

wicketData = Over_W.map(train_create)
runsData = Over_R.map(train_create)

print(wicketData)

PythonRDD[59] at RDD at PythonRDD.scala:52


In [6]:
def getBatsmanStat(name):
    player = Bat_Clus[Bat_Clus['Player Name']==name]
    if(player.empty):
        l = np.array(Bat_Clus.mean())
    else:
        player.drop('Player Name', axis=1, inplace=True)
        l = np.array(player.values[0])
    return l
        
def getBowlerStat(name):
    player = Bowl_Clus[Bowl_Clus['Player Name']==name]
    if(player.empty):
        l = np.array(Bowl_Clus.mean())
    else:
        player.drop('Player Name', axis=1, inplace=True)
        l = np.array(player.values[0])
    return l

#getBowlerStat('DJ Bravo')
getBatsmanStat('DJ Bravo')

array([1.52048193e+01, 1.26326326e+02, 1.50909091e+00, 4.80480480e-02,
       1.03103103e-01])

In [7]:
wicketModel = DecisionTree.trainRegressor(wicketData, impurity='variance',categoricalFeaturesInfo={}, maxDepth=30, maxBins=40)
print(wicketModel.toDebugString())



DecisionTreeModel regressor of depth 30 with 13473 nodes
  If (feature 0 <= 16.5)
   If (feature 0 <= 12.5)
    If (feature 7 <= 24.095238095238)
     If (feature 1 <= 15.8125)
      If (feature 7 <= 16.042857142857)
       If (feature 11 <= 0.06486676)
        If (feature 11 <= 0.0203176565)
         If (feature 6 <= 7.2412989309541)
          If (feature 1 <= 14.033333335)
           Predict: 0.0
          Else (feature 1 > 14.033333335)
           Predict: 1.0
         Else (feature 6 > 7.2412989309541)
          If (feature 0 <= 0.5)
           Predict: 0.0
          Else (feature 0 > 0.5)
           If (feature 4 <= 0.0740904515)
            If (feature 1 <= 6.354166666499999)
             Predict: 1.0
            Else (feature 1 > 6.354166666499999)
             Predict: 0.0
           Else (feature 4 > 0.0740904515)
            If (feature 0 <= 5.5)
             If (feature 0 <= 1.5)
              Predict: 1.0
             Else (feature 0 > 1.5)
              Predict: 2.0
      

In [8]:
runsModel = DecisionTree.trainRegressor(runsData, impurity='variance',categoricalFeaturesInfo={}, maxDepth=30, maxBins=40)
print(runsModel.toDebugString())

DecisionTreeModel regressor of depth 30 with 38369 nodes
  If (feature 0 <= 13.5)
   If (feature 6 <= 8.415706008540699)
    If (feature 0 <= 1.5)
     If (feature 2 <= 124.304317)
      If (feature 0 <= 0.5)
       If (feature 3 <= 0.059114936)
        If (feature 8 <= 0.44097222222222)
         If (feature 10 <= 138.42809365)
          If (feature 8 <= 0.32795698924731)
           If (feature 3 <= 0.0237390815)
            Predict: 2.0
           Else (feature 3 > 0.0237390815)
            If (feature 2 <= 122.9504019)
             If (feature 1 <= 13.27011494)
              Predict: 7.0
             Else (feature 1 > 13.27011494)
              If (feature 1 <= 20.78104974)
               Predict: 5.0
              Else (feature 1 > 20.78104974)
               Predict: 6.0
            Else (feature 2 > 122.9504019)
             Predict: 2.0
          Else (feature 8 > 0.32795698924731)
           If (feature 5 <= 32.803763440859996)
            If (feature 9 <= 21.42039801)
         

In [9]:
import random
random.seed(20)

def matchSimulation(inn1Ba,inn1Bo,inn2Ba,inn2Bo):
    batting=[inn1Ba,inn2Ba]
    bowling=[inn2Bo,inn1Bo]
    match=[[],[]]
    runPerInn=[0,0]
    wicketCount=[0,0]
    strike={}
    offStrike={}
    bowler={}    
    for inn in range(2):
        strike['name']=batting[inn][0]
        offStrike['name']=batting[inn][1]
        
        for over in range(20):
            bowler['name']=bowling[inn][over%len(bowling[inn])]
            strike['data']= getBatsmanStat(strike['name'])
            offStrike['data']=getBatsmanStat(offStrike['name'])
            bowler['data']=getBowlerStat(bowler['name'])
            overData=[over]
            overData.extend(strike['data'])
            overData.extend(offStrike['data'])
            overData.extend(bowler['data'])
            
            runs=round(runsModel.predict(overData)*(random.uniform(1,1.2)))
            wickets=round(wicketModel.predict(overData)*(random.uniform(1,1.25)))
            match[inn].append([strike['name'],offStrike['name'],bowler['name'],runs,wickets])
            if(wickets):
                runs=round((runs/6)*(6-wickets))
                if((wicketCount[inn]+wickets)>=10):
                    wicketCount[inn]=10
                    runPerInn[inn]+=runs
                    match[inn].append([strike['name'],offStrike['name'],runs,'all out']) 
                    break;
                wicketCount[inn]+=wickets  
                strike['name']=batting[inn][wicketCount[inn]+1]
                
            runPerInn[inn]+=runs
            if(runPerInn[1]>runPerInn[0]):
                break
            strike,offStrike= offStrike,strike
    for i in match[0]:
        print(i)
    print('\n\n')
    for i in match[1]:
        print(i)
    print("\n1st Innings: ",runPerInn[0],"/",wicketCount[0])
    print("\n2nd Innings: ",runPerInn[1],"/",wicketCount[1])

In [10]:
t1bat=['LMP Simmons','PA Patel','AT Rayudu','RG Sharma','KH Pandya','KA Pollard','HH Pandya','KV Sharma','MG Johnson','JJ Bumrah','SL Malinga']
t2bowl=['JD Unadkat','Washington Sundar','JD Unadkat','Washington Sundar','JD Unadkat','DT Christian','SN Thakur','DT Christian','A Zampa','LH Ferguson','A Zampa','LH Ferguson','A Zampa','Washington Sundar','A Zampa','Washington Sundar','DT Christian','SN Thakur','JD Unadkat','DT Christian']

t2bat=['AM Rahane','RA Tripathi','SPD Smith','MS Dhoni','MK Tiwary','DT Christian','Washington Sundar','LH Ferguson','A Zampa','SN Thakur','JD Unadkat']
t1bowl=['KH Pandya','MG Johnson','JJ Bumrah','SL Malinga','KV Sharma','KH Pandya','MG Johnson','JJ Bumrah','SL Malinga','KV Sharma','KH Pandya','MG Johnson','JJ Bumrah','SL Malinga','KV Sharma','KH Pandya','MG Johnson','JJ Bumrah','SL Malinga','KV Sharma']

matchSimulation(t1bat, t1bowl, t2bat, t2bowl)

['LMP Simmons', 'PA Patel', 'JD Unadkat', 4, 0]
['PA Patel', 'LMP Simmons', 'Washington Sundar', 10, 0]
['LMP Simmons', 'PA Patel', 'JD Unadkat', 9, 0]
['PA Patel', 'LMP Simmons', 'Washington Sundar', 8, 0]
['LMP Simmons', 'PA Patel', 'JD Unadkat', 8, 0]
['PA Patel', 'LMP Simmons', 'DT Christian', 8, 0]
['LMP Simmons', 'PA Patel', 'SN Thakur', 7, 0]
['PA Patel', 'LMP Simmons', 'DT Christian', 8, 0]
['LMP Simmons', 'PA Patel', 'A Zampa', 7, 0]
['PA Patel', 'LMP Simmons', 'LH Ferguson', 8, 0]
['LMP Simmons', 'PA Patel', 'A Zampa', 8, 0]
['PA Patel', 'LMP Simmons', 'LH Ferguson', 8, 0]
['LMP Simmons', 'PA Patel', 'A Zampa', 7, 0]
['PA Patel', 'LMP Simmons', 'Washington Sundar', 7, 1]
['LMP Simmons', 'AT Rayudu', 'A Zampa', 31, 1]
['AT Rayudu', 'RG Sharma', 'Washington Sundar', 5, 1]
['RG Sharma', 'KH Pandya', 'DT Christian', 14, 1]
['KH Pandya', 'KA Pollard', 'SN Thakur', 9, 0]
['KA Pollard', 'KH Pandya', 'JD Unadkat', 16, 0]
['KH Pandya', 'KA Pollard', 'DT Christian', 13, 1]



['AM Raha

In [11]:
match1={
"team1_batting_order":["SR Watson","AT Rayudu","SK Raina","SW Billings","RA Jadeja","MS Dhoni","DJ Bravo","Harbhajan Singh","DL Chahar","SN Thakur","Imran Tahir"],
"team2_batting_order":["AS Yadav","SR Tendulkar","Ishan Kishan","RG Sharma","JP Duminy","KH Pandya","HH Pandya","BCJ Cutting","MJ McClenaghan","SL Malinga","JJ Bumrah"],
"team1_bowling_order":["DL Chahar","SN Thakur","DL Chahar","SR Watson","DL Chahar","SN Thakur","SR Watson","Harbhajan Singh","Imran Tahir","Harbhajan Singh","Imran Tahir","Harbhajan Singh","DJ Bravo","SR Watson","DJ Bravo","SN Thakur","DJ Bravo","SR Watson","SN Thakur","Imran Tahir"],
"team2_bowling_order":["MJ McClenaghan","JJ Bumrah","MJ McClenaghan","HH Pandya","KH Pandya","HH Pandya","KH Pandya","SL Malinga","BCJ Cutting","SL Malinga","MJ McClenaghan","KH Pandya","JJ Bumrah","KH Pandya","HH Pandya","SL Malinga","JJ Bumrah","MJ McClenaghan","JJ Bumrah","HH Pandya"]
}
#

#2.SRH vs CSK 27 may - 178/6 vs 181/2
match2={
"team1_batting_order":["SP Goswami","S Dhawan","KS Williamson","Shakib Al Hasan","YK Pathan","DJ Hooda","CR Brathwaite","Rashid Khan","B Kumar","S Kaul","Sandeep Sharma"],
"team2_batting_order":["SR Watson","F du Plessis","SK Raina","AT Rayudu","MS Dhoni","DJ Bravo","RA Jadeja","KV Sharma","DL Chahar","SN Thakur","L Ngidi"],
"team1_bowling_order":["B Kumar","Sandeep Sharma","B Kumar","Sandeep Sharma","B Kumar","Sandeep Sharma","S Kaul","Rashid Khan","S Kaul","Rashid Khan","Shakib Al Hasan","CR Brathwaite","Sandeep Sharma","CR Brathwaite","Rashid Khan","B Kumar","Rashid Khan","S Kaul","CR Brathwaite","S Kaul"],
"team2_bowling_order":["DL Chahar","L Ngidi","DL Chahar","L Ngidi","DL Chahar","SN Thakur","KV Sharma","DJ Bravo","RA Jadeja","DL Chahar","RA Jadeja","DJ Bravo","KV Sharma","SN Thakur","KV Sharma","DJ Bravo","L Ngidi","DJ Bravo","L Ngidi","SN Thakur"]
}

#3.SRH vs CSK 22 may - 139/7 vs 140/8
match3={
"team2_bowling_order":["DL Chahar","L Ngidi","DL Chahar","L Ngidi","SN Thakur","DL Chahar","DJ Bravo","RA Jadeja","DJ Bravo","RA Jadeja","DL Chahar","RA Jadeja","SN Thakur","RA Jadeja","DJ Bravo","L Ngidi","DJ Bravo","SN Thakur","L Ngidi","SN Thakur"],
"team1_bowling_order":["B Kumar","Sandeep Sharma","B Kumar","S Kaul","B Kumar","S Kaul","CR Brathwaite","Rashid Khan","CR Brathwaite","Rashid Khan","Shakib Al Hasan","Rashid Khan","Sandeep Sharma","Shakib Al Hasan","Sandeep Sharma","Rashid Khan","S Kaul","CR Brathwaite","S Kaul","B Kumar"],
"team1_batting_order":["S Dhawan","SP Goswami","KS Williamson","MK Pandey","Shakib Al Hasan","YK Pathan","CR Brathwaite","B Kumar","Rashid Khan","S Kaul","Sandeep Sharma"],
"team2_batting_order":["SR Watson","F du Plessis","SK Raina","AT Rayudu","MS Dhoni","DJ Bravo","RA Jadeja","DL Chahar","Harbhajan Singh","SN Thakur","L Ngidi"]
}



#4.SRH vs CSK 13 may - 179/4 vs 180/2
match4={
"team1_bowling_order":["Sandeep Sharma","B Kumar","Sandeep Sharma","B Kumar","Rashid Khan","Shakib Al Hasan","S Kaul","Shakib Al Hasan","Rashid Khan","Sandeep Sharma","S Kaul","Rashid Khan","B Kumar","Shakib Al Hasan","Sandeep Sharma","Shakib Al Hasan","Rashid Khan","S Kaul","B Kumar","S Kaul"],
"team2_bowling_order":["DL Chahar","SN Thakur","DJ Wiley","DL Chahar","SN Thakur","DL Chahar","Harbhajan Singh","DL Chahar","SR Watson","DJ Bravo","RA Jadeja","SR Watson","RA Jadeja","Harbhajan Singh","DJ Wiley","DJ Bravo","SN Thakur","DJ Bravo","SN Thakur","DJ Bravo"],
"team2_batting_order":["SR Watson","AT Rayudu","SK Raina","MS Dhoni","SW Billings","DJ Bravo","RA Jadeja","DJ Wiley","Harbhajan Singh","DL Chahar","SN Thakur"],
"team1_batting_order":["S Dhawan","AD Hales","KS Williamson","MK Pandey","DJ Hooda","Shakib Al Hasan","SP Goswami","Rashid Khan","B Kumar","S Kaul","Sandeep Sharma"]
}



#5.CSK vs SRH 22 Apr 182/3 vs 178/6
match5={
"team1_batting_order":["SR Watson","F du Plessis","SK Raina","AT Rayudu","MS Dhoni","SW Billings","DJ Bravo","RA Jadeja","DL Chahar","KV Sharma","SN Thakur"],
"team2_batting_order":["RK Bhui","KS Williamson","MK Pandey","DJ Hooda","Shakib Al Hasan","YK Pathan","WP Saha","Rashid Khan","B Kumar","B Stanlake","S Kaul"],
"team1_bowling_order":["DL Chahar","SN Thakur","DL Chahar","SN Thakur","DL Chahar","SR Watson","RA Jadeja","DL Chahar","RA Jadeja","SR Watson","KV Sharma","RA Jadeja","KV Sharma","RA Jadeja","KV Sharma","DJ Bravo","SN Thakur","DJ Bravo","SN Thakur","DJ Bravo"],
"team2_bowling_order":["B Kumar","B Stanlake","Shakib Al Hasan","B Kumar","B Stanlake","S Kaul","Shakib Al Hasan","Rashid Khan","S Kaul","B Kumar","DJ Hooda","Rashid Khan","Shakib Al Hasan","B Stanlake","Shakib Al Hasan","Rashid Khan","S Kaul","Rashid Khan","S Kaul","B Stanlake"]
}

In [12]:
matchSimulation(match1["team1_batting_order"],match1["team1_bowling_order"],match1["team2_batting_order"],match1["team2_bowling_order"])

['SR Watson', 'AT Rayudu', 'MJ McClenaghan', 3, 0]
['AT Rayudu', 'SR Watson', 'JJ Bumrah', 10, 0]
['SR Watson', 'AT Rayudu', 'MJ McClenaghan', 9, 0]
['AT Rayudu', 'SR Watson', 'HH Pandya', 7, 0]
['SR Watson', 'AT Rayudu', 'KH Pandya', 7, 0]
['AT Rayudu', 'SR Watson', 'HH Pandya', 8, 0]
['SR Watson', 'AT Rayudu', 'KH Pandya', 7, 0]
['AT Rayudu', 'SR Watson', 'SL Malinga', 7, 0]
['SR Watson', 'AT Rayudu', 'BCJ Cutting', 8, 0]
['AT Rayudu', 'SR Watson', 'SL Malinga', 7, 0]
['SR Watson', 'AT Rayudu', 'MJ McClenaghan', 7, 0]
['AT Rayudu', 'SR Watson', 'KH Pandya', 8, 0]
['SR Watson', 'AT Rayudu', 'JJ Bumrah', 8, 0]
['AT Rayudu', 'SR Watson', 'KH Pandya', 7, 1]
['SR Watson', 'SK Raina', 'HH Pandya', 23, 1]
['SK Raina', 'SW Billings', 'SL Malinga', 8, 1]
['SW Billings', 'RA Jadeja', 'JJ Bumrah', 2, 1]
['RA Jadeja', 'MS Dhoni', 'MJ McClenaghan', 2, 0]
['MS Dhoni', 'RA Jadeja', 'JJ Bumrah', 9, 0]
['RA Jadeja', 'MS Dhoni', 'HH Pandya', 2, 2]



['AS Yadav', 'SR Tendulkar', 'DL Chahar', 3, 2]
['S

In [13]:
matchSimulation(match2["team1_batting_order"],match2["team1_bowling_order"],match2["team2_batting_order"],match2["team2_bowling_order"])

['SP Goswami', 'S Dhawan', 'DL Chahar', 4, 0]
['S Dhawan', 'SP Goswami', 'L Ngidi', 11, 0]
['SP Goswami', 'S Dhawan', 'DL Chahar', 10, 0]
['S Dhawan', 'SP Goswami', 'L Ngidi', 8, 0]
['SP Goswami', 'S Dhawan', 'DL Chahar', 7, 0]
['S Dhawan', 'SP Goswami', 'SN Thakur', 7, 0]
['SP Goswami', 'S Dhawan', 'KV Sharma', 8, 0]
['S Dhawan', 'SP Goswami', 'DJ Bravo', 7, 0]
['SP Goswami', 'S Dhawan', 'RA Jadeja', 7, 0]
['S Dhawan', 'SP Goswami', 'DL Chahar', 7, 0]
['SP Goswami', 'S Dhawan', 'RA Jadeja', 7, 0]
['S Dhawan', 'SP Goswami', 'DJ Bravo', 7, 0]
['SP Goswami', 'S Dhawan', 'KV Sharma', 7, 0]
['S Dhawan', 'SP Goswami', 'SN Thakur', 8, 1]
['SP Goswami', 'KS Williamson', 'KV Sharma', 8, 1]
['KS Williamson', 'Shakib Al Hasan', 'DJ Bravo', 6, 1]
['Shakib Al Hasan', 'YK Pathan', 'L Ngidi', 2, 1]
['YK Pathan', 'DJ Hooda', 'DJ Bravo', 12, 0]
['DJ Hooda', 'YK Pathan', 'L Ngidi', 15, 1]
['YK Pathan', 'CR Brathwaite', 'SN Thakur', 16, 1]



['SR Watson', 'F du Plessis', 'B Kumar', 3, 0]
['F du Plessis

In [14]:
matchSimulation(match3["team2_batting_order"],match3["team2_bowling_order"],match3["team1_batting_order"],match3["team1_bowling_order"])

['SR Watson', 'F du Plessis', 'B Kumar', 3, 0]
['F du Plessis', 'SR Watson', 'Sandeep Sharma', 9, 0]
['SR Watson', 'F du Plessis', 'B Kumar', 10, 0]
['F du Plessis', 'SR Watson', 'S Kaul', 8, 0]
['SR Watson', 'F du Plessis', 'B Kumar', 8, 0]
['F du Plessis', 'SR Watson', 'S Kaul', 8, 0]
['SR Watson', 'F du Plessis', 'CR Brathwaite', 7, 0]
['F du Plessis', 'SR Watson', 'Rashid Khan', 7, 0]
['SR Watson', 'F du Plessis', 'CR Brathwaite', 7, 0]
['F du Plessis', 'SR Watson', 'Rashid Khan', 8, 0]
['SR Watson', 'F du Plessis', 'Shakib Al Hasan', 7, 0]
['F du Plessis', 'SR Watson', 'Rashid Khan', 8, 0]
['SR Watson', 'F du Plessis', 'Sandeep Sharma', 8, 0]
['F du Plessis', 'SR Watson', 'Shakib Al Hasan', 7, 1]
['SR Watson', 'SK Raina', 'Sandeep Sharma', 23, 1]
['SK Raina', 'AT Rayudu', 'Rashid Khan', 8, 1]
['AT Rayudu', 'MS Dhoni', 'S Kaul', 2, 1]
['MS Dhoni', 'DJ Bravo', 'CR Brathwaite', 10, 0]
['DJ Bravo', 'MS Dhoni', 'S Kaul', 2, 0]
['MS Dhoni', 'DJ Bravo', 'B Kumar', 12, 1]



['S Dhawan', 

In [15]:
matchSimulation(match4["team1_batting_order"],match4["team1_bowling_order"],match4["team2_batting_order"],match4["team2_bowling_order"])

['S Dhawan', 'AD Hales', 'DL Chahar', 4, 0]
['AD Hales', 'S Dhawan', 'SN Thakur', 9, 0]
['S Dhawan', 'AD Hales', 'DJ Wiley', 10, 0]
['AD Hales', 'S Dhawan', 'DL Chahar', 8, 0]
['S Dhawan', 'AD Hales', 'SN Thakur', 7, 0]
['AD Hales', 'S Dhawan', 'DL Chahar', 7, 0]
['S Dhawan', 'AD Hales', 'Harbhajan Singh', 8, 0]
['AD Hales', 'S Dhawan', 'DL Chahar', 7, 0]
['S Dhawan', 'AD Hales', 'SR Watson', 8, 0]
['AD Hales', 'S Dhawan', 'DJ Bravo', 7, 0]
['S Dhawan', 'AD Hales', 'RA Jadeja', 8, 0]
['AD Hales', 'S Dhawan', 'SR Watson', 8, 0]
['S Dhawan', 'AD Hales', 'RA Jadeja', 7, 0]
['AD Hales', 'S Dhawan', 'Harbhajan Singh', 8, 0]
['S Dhawan', 'AD Hales', 'DJ Wiley', 24, 1]
['AD Hales', 'KS Williamson', 'DJ Bravo', 7, 0]
['KS Williamson', 'AD Hales', 'SN Thakur', 15, 1]
['AD Hales', 'MK Pandey', 'DJ Bravo', 7, 1]
['MK Pandey', 'DJ Hooda', 'SN Thakur', 15, 0]
['DJ Hooda', 'MK Pandey', 'DJ Bravo', 15, 2]



['SR Watson', 'AT Rayudu', 'Sandeep Sharma', 3, 0]
['AT Rayudu', 'SR Watson', 'B Kumar', 11, 

In [16]:
matchSimulation(match5["team1_batting_order"],match5["team1_bowling_order"],match5["team2_batting_order"],match5["team2_bowling_order"])

['SR Watson', 'F du Plessis', 'B Kumar', 3, 0]
['F du Plessis', 'SR Watson', 'B Stanlake', 10, 0]
['SR Watson', 'F du Plessis', 'Shakib Al Hasan', 10, 0]
['F du Plessis', 'SR Watson', 'B Kumar', 7, 0]
['SR Watson', 'F du Plessis', 'B Stanlake', 7, 0]
['F du Plessis', 'SR Watson', 'S Kaul', 8, 0]
['SR Watson', 'F du Plessis', 'Shakib Al Hasan', 8, 0]
['F du Plessis', 'SR Watson', 'Rashid Khan', 8, 0]
['SR Watson', 'F du Plessis', 'S Kaul', 8, 0]
['F du Plessis', 'SR Watson', 'B Kumar', 7, 0]
['SR Watson', 'F du Plessis', 'DJ Hooda', 7, 0]
['F du Plessis', 'SR Watson', 'Rashid Khan', 8, 0]
['SR Watson', 'F du Plessis', 'Shakib Al Hasan', 8, 0]
['F du Plessis', 'SR Watson', 'B Stanlake', 8, 1]
['SR Watson', 'SK Raina', 'Shakib Al Hasan', 22, 1]
['SK Raina', 'AT Rayudu', 'Rashid Khan', 8, 1]
['AT Rayudu', 'MS Dhoni', 'S Kaul', 2, 1]
['MS Dhoni', 'SW Billings', 'Rashid Khan', 9, 0]
['SW Billings', 'MS Dhoni', 'S Kaul', 2, 0]
['MS Dhoni', 'SW Billings', 'B Stanlake', 13, 1]



['RK Bhui', 'K